# Tối Ưu Hóa Ưu Tiên Theo Tỷ Lệ Odds (Odds Ratio Preference Optimization - ORPO)

Bài tập này sẽ hướng dẫn bạn quy trình tinh chỉnh mô hình ngôn ngữ sử dụng phương pháp ORPO. Chúng ta sẽ sử dụng mô hình `HuggingFaceTB/SmolLM2-135M` bản gốc (chưa được huấn luyện SFT), nên nó không tương thích với DPO. Điều này có nghĩa là bạn không thể sử dụng mô hình bạn đã huấn luyện trong [1_instruction_tuning](../../1_instruction_tuning/notebooks/sft_finetuning_example.ipynb).

<div style='background-color: lightblue; padding: 10px; border-radius: 5px; margin-bottom: 20px; color:black'>
     <h2 style='margin: 0;color:blue'>Bài tập: Tinh chỉnh SmolLM2 với DPOTrainer</h2>
     <p>Lấy một tập bộ liệu từ Hugging Face hub và điều chỉnh mô hình trên bộ dữ liệu đó. </p> 
     <p><b>Các bài tập</b></p>
     <p>🐢 Sử dụng bộ dữ liệu `trl-lib/ultrafeedback_binarized`</p>
     <p>🐕 Thử nghiệm với bộ dữ liệu `argilla/ultrafeedback-binarized-preferences`</p>
     <p>🦁 Thử nghiệm với một phần của bộ dữ liệu `orpo-dpo-mix-40k` của mlabonne</p>
</div>



In [ ]:
# Các thư viện cần thiết

import torch
import os
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
)
from trl import ORPOConfig, ORPOTrainer, setup_chat_format

# Authenticate to Hugging Face
from huggingface_hub import login

login()

/Users/ben/code/smol-course/.venv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Chuẩn bị dữ liệu

In [ ]:
# Tải tập dữ liệu

# TODO: 🦁🐕 thay đổi tập dữ liệu theo lựa chọn của bạn
dataset = load_dataset(path="trl-lib/ultrafeedback_binarized", split="train")

Generating test split: 100%|██████████| 1000/1000 [00:00<00:00, 382866.64 examples/s]


In [ ]:
# TODO: 🐕 Nếu bộ dữ liệu của bạn không được biểu diễn dưới dạng danh sách hội thoại,
# bạn có thể sử dụng hàm `process_dataset` để chuyển đổi nó.

In [ ]:
## Chọn mô hình

model_name = "HuggingFaceTB/SmolLM2-135M"

device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps" if torch.backends.mps.is_available() else "cpu"
)

# Mô hình để tinh chỉnh
model = AutoModelForCausalLM.from_pretrained(
    pretrained_model_name_or_path=model_name,
    torch_dtype=torch.float16,
).to(device)
model.config.use_cache = False
tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token

# Đặt tên cho bản tinh chỉnh để lưu &/ tải lên
finetune_name = "SmolLM2-FT-ORPO"
finetune_tags = ["smol-course", "module_2"]

## Huấn luyện mô hình với ORPO

In [ ]:
orpo_args = ORPOConfig(
    # Learning rate nhỏ để tránh catastrophic forgetting
    # Đọc thêm về catastrophic forgetting: https://blog.vinbigdata.org/robot-co-the-hoc-suot-doi-khong/
    learning_rate=8e-6,
    # Giảm learning rate tuyến tính trong quá trình huấn luyện
    lr_scheduler_type="linear",
    # Độ dài tối đa kết hợp của chỉ thị + câu trả lời
    max_length=1024,
    # Độ dài tối đa cho input prompts
    max_prompt_length=512,
    # Kiểm soát trọng số của hàm mất mát odds ratio (λ trong paper)
    beta=0.1,
    # Kích thước batch cho huấn luyện
    per_device_train_batch_size=2,
    per_device_eval_batch_size=2,
    # Giúp ổn định quá trình huấn luyện bằng cách tích luỹ gradient trước khi cập nhật
    gradient_accumulation_steps=4,
    # Optimizer tiết kiệm bộ nhớ cho CUDA, sử dụng adamw_torch cho CPU/MPS
    optim="paged_adamw_8bit" if device == "cuda" else "adamw_torch",
    # Số epoch huấn luyện
    num_train_epochs=1,
    # Khi nào chạy đánh giá
    evaluation_strategy="steps",
    # Đánh giá sau mỗi 20% huấn luyện
    eval_steps=0.2,
    # Ghi log metrics mỗi step
    logging_steps=1,
    # Tăng learning rate dần dần
    warmup_steps=10,
    # Tắt logging bên ngoài
    report_to="none",
    # Nơi lưu model/checkpoints
    output_dir="./results/",
    # Bật MPS (Metal Performance Shaders) nếu có
    use_mps_device=device == "mps",
    hub_model_id=finetune_name,
)

In [ ]:
trainer = ORPOTrainer(
    model=model,
    args=orpo_args,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    processing_class=tokenizer,
)

In [ ]:
trainer.train()  # Huấn luyện mô hình

# Lưu mô hình
trainer.save_model(f"./{finetune_name}")

# Lưu lên huggingface hub nếu đã đăng nhập (HF_TOKEN đã được thiết lập)
if os.getenv("HF_TOKEN"):
    trainer.push_to_hub(tags=finetune_tags)

## 💐 Bạn đã hoàn thành!

Bài tập này đã hướng dẫn bạn từng bước cách tinh chỉnh mô hình `HuggingFaceTB/SmolLM2-135M` sử dụng `ORPOTrainer`. Theo các bước này, bạn có thể điều chỉnh mô hình để thực hiện các tác vụ cụ thể một cách hiệu quả hơn. Nếu bạn muốn tiếp tục học khóa học này, đây là một số bước bạn có thể thử:

- Thử bài tập này ở các mức độ khó hơn
- Đánh giá PR của bạn học khác
- Cải thiện khóa học thông qua Issue hoặc PR